In [32]:
from mpa.models import Mpa, mpa_post_save
from django.db.models.signals import post_save, post_delete
from mpa.views import mpas_all_nogeom
import reversion
from reversion.models import Revision
from reversion.models import Version
import datetime
from django.db.models import Q, F, Func
from wdpa.models import Wdpa2019Poly, Wdpa2019Point

In [33]:
mpaset = mpas_all_nogeom.exclude(
        Q(country__icontains='USA') | Q(sovereign__icontains='USA') |
        Q(country__icontains='UMI') | Q(sovereign__icontains='UMI') |
        Q(country__icontains='VIR') | Q(sovereign__icontains='VIR') |
        Q(country__icontains='PRI') | Q(sovereign__icontains='PRI') |
        Q(country__icontains='ASM') | Q(sovereign__icontains='ASM') |
        Q(country__icontains='GUM') | Q(sovereign__icontains='GUM') |
        Q(country__icontains='MNP') | Q(sovereign__icontains='MNP')
    ).exclude(
        Q(country__icontains='MEX') | Q(country__icontains='CHL') | Q(country__icontains='IDN') | 
        Q(country__icontains='CHN') | Q(country__icontains='JPN') | 
        Q(sovereign__icontains='MEX') | Q(sovereign__icontains='CHL') | Q(sovereign__icontains='IDN') |
        Q(sovereign__icontains='CHN') | Q(sovereign__icontains='JPN')
    )
mpaset.values('country').distinct()

<QuerySet [{'country': 'ABNJ'}, {'country': 'MDG'}, {'country': 'TZA'}, {'country': 'PLW'}, {'country': 'GGY'}, {'country': 'NLD'}, {'country': 'VEN'}, {'country': 'BMU'}, {'country': 'FIN/SWE'}, {'country': 'COG'}, {'country': 'CUB'}, {'country': 'MAF'}, {'country': 'IRL'}, {'country': 'GIB'}, {'country': 'IOT'}, {'country': 'ISR'}, {'country': 'GBR'}, {'country': 'BGD/IND'}, {'country': 'GMB'}, {'country': 'MMR'}, '...(remaining elements truncated)...']>

In [4]:
# mpaset = mpas_all_nogeom.exclude(
#         Q(country__icontains='USA') | Q(sovereign__icontains='USA') |
#         Q(country__icontains='UMI') | Q(sovereign__icontains='UMI') |
#         Q(country__icontains='VIR') | Q(sovereign__icontains='VIR') |
#         Q(country__icontains='PRI') | Q(sovereign__icontains='PRI') |
#         Q(country__icontains='ASM') | Q(sovereign__icontains='ASM') |
#         Q(country__icontains='GUM') | Q(sovereign__icontains='GUM') |
#         Q(country__icontains='MNP') | Q(sovereign__icontains='MNP')
#     ).exclude(
#         Q(country__icontains='MEX') | Q(country__icontains='CHL') | Q(country__icontains='IDN') | 
#         Q(country__icontains='CHN') | Q(country__icontains='JPN') | 
#         Q(sovereign__icontains='MEX') | Q(sovereign__icontains='CHL') | Q(sovereign__icontains='IDN') |
#         Q(sovereign__icontains='CHN') | Q(sovereign__icontains='JPN')
#     ).exclude(
#         Q(country__icontains='FRA') | Q(sovereign__icontains='FRA') |
#         Q(country__icontains='ATF') | Q(country__icontains='BLM') | Q(country__icontains='GLP') |
#         Q(country__icontains='GUF') | Q(country__icontains='MAF') | Q(country__icontains='MTQ') |
#         Q(country__icontains='MYT') | Q(country__icontains='NCL') | Q(country__icontains='PYF') |
#         Q(country__icontains='REU') | Q(country__icontains='SHN') | Q(country__icontains='SYC')
#     ).exclude(
#         Q(country__icontains='AUS') | Q(sovereign__icontains='AUS') |
#         Q(country__icontains='ZAF') | Q(sovereign__icontains='ZAF') |
#         Q(country__icontains='CAN') | Q(sovereign__icontains='CAN')
#     ).exclude(
#         Q(country__icontains='GBR') | Q(sovereign__icontains='GBR') |
#         Q(country__icontains='AIA') | Q(country__icontains='BMU') | Q(country__icontains='CYM') |
#         Q(country__icontains='FLK') | Q(country__icontains='GIB') | Q(country__icontains='IMN') |
#         Q(country__icontains='IOT') | Q(country__icontains='JEY') | Q(country__icontains='MSR') |
#         Q(country__icontains='PCN') | Q(country__icontains='SGS') | Q(country__icontains='SHN') |
#         Q(country__icontains='TCA') | Q(country__icontains='VGB')
#     )
# mpaset.values('country').distinct()

In [4]:
mpas_all_nogeom.filter(wdpa_id=0).update(wdpa_id=None)
mpas_all_nogeom.filter(wdpa_id=0).count()

0

In [5]:
count = 0
# cutoff_date = datetime.datetime(2014, 11, 5)
cutoff_date = datetime.datetime(2018, 10, 15)
for m in mpaset:
    versions = Version.objects.get_for_object(m)
    created = 'Never'
    if not m.wdpa_id: continue
    try:
        created = versions.first().revision.date_created
        if created > cutoff_date:
            count = count + 1
            print(count, created, 'count:', len(versions), 'mpa_id:', m.mpa_id, 'wdpa_id:', m.wdpa_id)
    except:
        pass

1 2018-10-26 04:22:08.294557 count: 2 mpa_id: 7702533 wdpa_id: 95310
2 2018-10-26 03:53:08.104390 count: 1 mpa_id: 68809929 wdpa_id: 555535858
3 2018-10-26 04:22:09.597028 count: 5 mpa_id: 143 wdpa_id: 959
4 2018-10-28 23:29:35.585177 count: 1 mpa_id: 68812688 wdpa_id: 555592987
5 2018-10-28 23:38:43.987531 count: 7 mpa_id: 6120 wdpa_id: 12263
6 2018-10-26 03:53:53.953959 count: 1 mpa_id: 68809959 wdpa_id: 555536079
7 2018-10-26 04:22:13.136130 count: 4 mpa_id: 144 wdpa_id: 960
8 2018-10-26 03:54:12.272421 count: 1 mpa_id: 68809974 wdpa_id: 555536244
9 2018-10-26 04:22:17.158248 count: 2 mpa_id: 145 wdpa_id: 962
10 2018-10-26 03:54:11.862717 count: 2 mpa_id: 5792 wdpa_id: 555536243
11 2018-10-28 23:38:59.789093 count: 3 mpa_id: 6406 wdpa_id: 17372
12 2018-10-28 23:53:47.737185 count: 2 mpa_id: 10228 wdpa_id: 155696
13 2018-10-28 23:24:58.860018 count: 1 mpa_id: 68812087 wdpa_id: 555555869
14 2018-10-17 10:04:37.880169 count: 1 mpa_id: 68808794 wdpa_id: 555548050
15 2019-01-25 09:53:28.

137 2018-10-26 04:14:56.203059 count: 2 mpa_id: 506 wdpa_id: 4879
138 2018-10-28 23:38:59.020057 count: 1 mpa_id: 6386 wdpa_id: 17150
139 2018-10-28 23:38:59.327644 count: 2 mpa_id: 6388 wdpa_id: 17188
140 2018-10-29 00:44:47.229997 count: 2 mpa_id: 13530 wdpa_id: 555537253
141 2018-10-29 00:20:09.563325 count: 2 mpa_id: 11723 wdpa_id: 384326
142 2018-10-28 23:35:18.603420 count: 1 mpa_id: 68813271 wdpa_id: 7941
143 2018-10-26 04:15:01.415721 count: 2 mpa_id: 511 wdpa_id: 4885
144 2018-10-28 23:33:03.313255 count: 1 mpa_id: 68813014 wdpa_id: 555623687
145 2018-10-29 00:29:22.916410 count: 2 mpa_id: 5584 wdpa_id: 555512398
146 2018-10-29 01:01:00.055567 count: 2 mpa_id: 15626 wdpa_id: 555577570
147 2018-10-29 00:24:39.988207 count: 2 mpa_id: 12174 wdpa_id: 396534
148 2018-10-28 23:34:18.544977 count: 1 mpa_id: 68813182 wdpa_id: 555635575
149 2018-10-29 00:09:51.657231 count: 2 mpa_id: 3725 wdpa_id: 302864
150 2018-10-24 15:06:19.348115 count: 2 mpa_id: 2170 wdpa_id: 67826
151 2018-10-28

261 2018-10-26 04:18:38.953837 count: 9 mpa_id: 15070 wdpa_id: 555559207
262 2018-10-29 00:13:31.171104 count: 6 mpa_id: 7097 wdpa_id: 315001
263 2018-10-23 17:00:59.795573 count: 2 mpa_id: 12776 wdpa_id: 555526141
264 2018-10-28 23:50:31.495592 count: 2 mpa_id: 3023 wdpa_id: 151896
265 2018-10-29 00:41:58.384255 count: 2 mpa_id: 13335 wdpa_id: 555532727
266 2018-10-29 01:08:58.728834 count: 4 mpa_id: 2221 wdpa_id: 67909
267 2018-10-28 23:57:30.719959 count: 2 mpa_id: 3277 wdpa_id: 156579
268 2018-10-17 10:10:09.421089 count: 2 mpa_id: 4360 wdpa_id: 309465
269 2018-10-26 04:02:39.402118 count: 1 mpa_id: 68810602 wdpa_id: 555624320
270 2018-10-28 23:39:37.243018 count: 2 mpa_id: 9544 wdpa_id: 555547638
271 2018-10-29 00:20:39.487787 count: 2 mpa_id: 11774 wdpa_id: 387968
272 2018-10-29 01:09:29.020167 count: 2 mpa_id: 2279 wdpa_id: 68056
273 2018-10-28 23:40:04.938993 count: 2 mpa_id: 9481 wdpa_id: 901259
274 2018-10-28 23:40:05.060491 count: 2 mpa_id: 7370 wdpa_id: 902319
275 2018-10-2

388 2018-10-23 16:53:11.593085 count: 1 mpa_id: 68809161 wdpa_id: 555624205
389 2018-10-28 23:39:13.983940 count: 2 mpa_id: 7124 wdpa_id: 315527
390 2018-10-28 23:39:14.065372 count: 2 mpa_id: 7125 wdpa_id: 315528
391 2018-10-23 16:53:15.086272 count: 1 mpa_id: 68809163 wdpa_id: 555624682
392 2018-10-28 23:34:19.667077 count: 1 mpa_id: 68813184 wdpa_id: 555635578
393 2018-10-28 23:33:53.658097 count: 1 mpa_id: 68813125 wdpa_id: 555625715
394 2018-10-23 16:53:17.786830 count: 1 mpa_id: 68809169 wdpa_id: 6270
395 2018-10-28 23:30:17.802449 count: 1 mpa_id: 68812745 wdpa_id: 555593065
396 2018-10-17 10:09:32.129399 count: 2 mpa_id: 11259 wdpa_id: 309628
397 2018-10-23 16:53:18.243747 count: 3 mpa_id: 559 wdpa_id: 6301
398 2018-10-24 15:06:33.445207 count: 4 mpa_id: 2594 wdpa_id: 99744
399 2018-10-28 23:39:22.638205 count: 3 mpa_id: 5917 wdpa_id: 3828
400 2018-10-29 00:10:44.198497 count: 4 mpa_id: 3881 wdpa_id: 305262
401 2018-10-28 23:18:29.066692 count: 1 mpa_id: 68811480 wdpa_id: 55552

520 2018-10-24 15:06:19.851553 count: 2 mpa_id: 2171 wdpa_id: 67833
521 2018-10-24 15:06:20.581578 count: 2 mpa_id: 2172 wdpa_id: 67835
522 2018-10-28 23:53:55.426889 count: 2 mpa_id: 10242 wdpa_id: 155801
523 2018-10-28 23:39:23.243306 count: 2 mpa_id: 5924 wdpa_id: 3964
524 2018-10-24 14:59:00.890194 count: 2 mpa_id: 11186 wdpa_id: 308310
525 2018-10-24 15:06:21.078942 count: 2 mpa_id: 2173 wdpa_id: 67836
526 2018-10-28 23:39:21.235461 count: 3 mpa_id: 5901 wdpa_id: 3674
527 2018-10-28 23:39:58.309464 count: 3 mpa_id: 5987 wdpa_id: 8500
528 2018-10-24 15:06:21.578746 count: 2 mpa_id: 2174 wdpa_id: 67837
529 2018-10-28 23:39:21.314396 count: 2 mpa_id: 5902 wdpa_id: 3679
530 2018-10-23 16:52:21.782148 count: 1 mpa_id: 68809078 wdpa_id: 555539271
531 2018-10-24 15:06:23.557303 count: 2 mpa_id: 2176 wdpa_id: 67839
532 2018-10-24 15:06:24.708894 count: 2 mpa_id: 2178 wdpa_id: 67842
533 2018-10-24 10:15:54.575586 count: 19 mpa_id: 67704841 wdpa_id: 315492
534 2018-10-24 15:06:25.273489 cou

...

15092 2018-10-26 04:12:41.204991 count: 5 mpa_id: 3582 wdpa_id: 220052
15093 2018-10-28 23:35:06.774033 count: 1 mpa_id: 68813248 wdpa_id: 61790
15094 2018-10-23 17:00:39.192503 count: 2 mpa_id: 13692 wdpa_id: 555539368
15095 2018-11-06 13:04:04.053899 count: 25 mpa_id: 7704395 wdpa_id: 309888
15096 2018-10-23 17:00:44.741804 count: 2 mpa_id: 12786 wdpa_id: 555526154
15097 2018-11-06 13:06:33.664155 count: 13 mpa_id: 4395 wdpa_id: 309888
15098 2018-10-29 00:12:02.260747 count: 4 mpa_id: 4022 wdpa_id: 306035
15099 2018-10-28 23:13:12.398180 count: 1 mpa_id: 68810934 wdpa_id: 19066
15100 2018-10-29 00:02:09.779574 count: 2 mpa_id: 10865 wdpa_id: 178500
15101 2018-10-28 23:35:07.107249 count: 1 mpa_id: 68813249 wdpa_id: 61791
15102 2018-10-28 23:53:32.804780 count: 2 mpa_id: 10204 wdpa_id: 155511
15103 2018-10-26 04:12:52.586540 count: 2 mpa_id: 7706938 wdpa_id: 220057
15104 2018-10-28 23:57:02.907198 count: 2 mpa_id: 10577 wdpa_id: 156433
15105 2018-10-28 23:13:06.745706 count: 1 mpa_id:

15206 2019-01-24 13:07:44.055467 count: 6 mpa_id: 15007 wdpa_id: 555556895
15207 2018-10-23 17:02:07.291005 count: 2 mpa_id: 12765 wdpa_id: 555526121
15208 2018-10-28 23:57:50.457358 count: 2 mpa_id: 10634 wdpa_id: 156660
15209 2018-10-29 00:57:04.370567 count: 5 mpa_id: 14702 wdpa_id: 555549171
15210 2018-10-29 00:10:46.963127 count: 4 mpa_id: 3895 wdpa_id: 305393
15211 2018-10-29 00:02:20.541032 count: 4 mpa_id: 3398 wdpa_id: 178838
15212 2018-10-23 17:02:00.983720 count: 2 mpa_id: 12773 wdpa_id: 555526138
15213 2018-10-29 00:16:49.238459 count: 2 mpa_id: 11475 wdpa_id: 339288
15214 2018-10-28 23:31:48.915589 count: 1 mpa_id: 68812856 wdpa_id: 555622138
15215 2018-10-26 03:46:41.151013 count: 1 mpa_id: 68809677 wdpa_id: 136122
15216 2018-10-26 04:14:06.336523 count: 2 mpa_id: 1723 wdpa_id: 28147
15217 2018-10-23 17:00:54.880466 count: 2 mpa_id: 12853 wdpa_id: 555526945
15218 2018-10-29 00:50:20.462872 count: 2 mpa_id: 13943 wdpa_id: 555541130
15219 2018-10-23 17:01:11.628676 count: 2

15334 2018-10-26 04:20:29.030526 count: 6 mpa_id: 7283 wdpa_id: 900634
15335 2018-10-26 04:20:33.117128 count: 4 mpa_id: 7299 wdpa_id: 900711
15336 2018-10-26 04:20:36.015110 count: 2 mpa_id: 7707299 wdpa_id: 900711
15337 2018-10-26 03:45:56.256966 count: 2 mpa_id: 927 wdpa_id: 12207
15338 2018-10-26 03:45:57.699470 count: 1 mpa_id: 1013 wdpa_id: 12896
15339 2018-10-26 03:45:59.482930 count: 1 mpa_id: 68809647 wdpa_id: 135143
15340 2018-10-26 04:13:00.942661 count: 2 mpa_id: 6944 wdpa_id: 220066
15341 2018-10-29 00:17:01.272486 count: 2 mpa_id: 11494 wdpa_id: 340094
15342 2018-10-29 00:44:56.487987 count: 2 mpa_id: 13542 wdpa_id: 555537295
15343 2018-10-29 00:32:05.022755 count: 2 mpa_id: 12600 wdpa_id: 555522518
15344 2018-10-28 23:32:57.196459 count: 1 mpa_id: 68813001 wdpa_id: 555623627
15345 2018-10-29 00:32:05.603116 count: 2 mpa_id: 5766 wdpa_id: 555522519
15346 2018-10-26 03:47:21.181317 count: 1 mpa_id: 68809702 wdpa_id: 137084
15347 2018-10-26 04:20:52.429897 count: 2 mpa_id: 

15456 2018-10-26 03:48:29.941714 count: 1 mpa_id: 68809751 wdpa_id: 139375
15457 2018-10-26 03:48:51.154750 count: 1 mpa_id: 68809776 wdpa_id: 139630
15458 2018-10-26 04:20:56.818957 count: 5 mpa_id: 2520 wdpa_id: 95291
15459 2018-10-26 03:48:53.140388 count: 1 mpa_id: 68809779 wdpa_id: 139656
15460 2018-10-26 03:48:55.519985 count: 1 mpa_id: 68809782 wdpa_id: 139680
15461 2018-10-29 01:11:44.056948 count: 4 mpa_id: 111 wdpa_id: 766
15462 2018-10-26 04:21:03.823542 count: 2 mpa_id: 7702521 wdpa_id: 95292
15463 2018-10-26 03:48:36.773483 count: 1 mpa_id: 68809756 wdpa_id: 139390
15464 2018-10-26 03:48:39.531911 count: 1 mpa_id: 68809761 wdpa_id: 139459
15465 2018-10-26 03:48:39.058930 count: 1 mpa_id: 68809760 wdpa_id: 139453
15466 2018-10-26 04:21:00.632029 count: 2 mpa_id: 7702520 wdpa_id: 95291
15467 2018-10-28 23:38:50.023903 count: 4 mpa_id: 6210 wdpa_id: 13248
15468 2018-10-26 03:49:15.772940 count: 1 mpa_id: 68809802 wdpa_id: 139821
15469 2018-10-26 03:49:16.595423 count: 1 mpa_i

15585 2018-10-28 23:56:48.706577 count: 2 mpa_id: 10552 wdpa_id: 156363
15586 2018-10-26 03:51:17.082393 count: 3 mpa_id: 3346 wdpa_id: 170242
15587 2018-10-26 04:22:04.748998 count: 4 mpa_id: 2531 wdpa_id: 95307
15588 2018-10-26 03:53:10.155962 count: 1 mpa_id: 68809930 wdpa_id: 555535859
15589 2018-10-26 03:51:20.381393 count: 1 mpa_id: 68809866 wdpa_id: 170243
15590 2018-10-26 03:51:22.023809 count: 3 mpa_id: 3389 wdpa_id: 174643
15591 2018-10-26 03:51:22.909912 count: 1 mpa_id: 68809867 wdpa_id: 174674
15592 2018-10-26 03:51:23.380587 count: 1 mpa_id: 68809868 wdpa_id: 174675
15593 2018-10-26 03:51:24.300787 count: 1 mpa_id: 68809869 wdpa_id: 174698
15594 2018-10-26 03:51:28.033827 count: 1 mpa_id: 68809872 wdpa_id: 174714
15595 2018-10-26 03:51:30.206934 count: 1 mpa_id: 68809873 wdpa_id: 174719
15596 2018-10-26 03:51:31.147537 count: 1 mpa_id: 68809874 wdpa_id: 174722
15597 2018-10-29 00:53:51.456742 count: 2 mpa_id: 14286 wdpa_id: 555544499
15598 2018-10-26 03:54:12.744134 count

In [34]:
from importlib import reload
from wdpa import merge
reload(merge)

<module 'wdpa.merge' from '/Users/russmo/Code/mpatlas-dj2/mpatlas/wdpa/merge.py'>

In [47]:
tas = Wdpa2019Poly.objects.filter(wdpa_pid__icontains='345888')
print(tas.count())
for t in tas:
    print(t.wdpaid, t.wdpa_pid, t.name, ',', t.desig, t.marine)

sgs = Wdpa2019Poly.objects.filter(name__icontains='South Georgia')
print(sgs.count())
for s in sgs:
    print(s.wdpaid, s.wdpa_pid, s.name, ',', s.desig, s.marine)


1
345888.0 345888 Terres Australes Françaises , Réserve Naturelle Nationale 2
1
555547601.0 555547601 South Georgia and South Sandwich Islands Marine Protected Area , Marine Protected Area 2


In [6]:
# remove_log = '/home/mpatlas/workspace/log/removewdpa_OTHER_log.json'
remove_log = '/Users/russmo/Code/wdpa/log/removewdpa_nonCEA_2019_log.json'
wdpa2remove = merge.getRemoveWdpaList(logfile=remove_log)

In [7]:
len(wdpa2remove)

0

In [8]:
rm_mpas = Mpa.objects.filter(wdpa_id__in=wdpa2remove).order_by('country')
len(rm_mpas)

0

In [11]:
for m in rm_mpas:
    print(m.mpa_id, m.wdpa_id, m.wdpa_pid, m.country, m.sovereign, m.is_mpa, m.no_take, m.no_take_area, m.name, m.designation_eng)

4104 306353 306353 CAN CAN False Not Reported 0.0 Aire de concentration d'oiseaux aquatiques de la Baie des Sept Îles 3 Water fowl gathering area
2606 100660 100660_A CAN CAN False Not Applicable 0.0 Kejimkujik National Park and National Historic Site of Canada  (Seaside Adjunct) National Park of Canada
15272 555569916 555569916 CAN CAN False Not Reported 0.0 Aire de concentration d'oiseaux aquatiques Le Long Pèlerin Water fowl gathering area
15238 555567616 555567616 CAN CAN False Not Reported 0.0 Aire de concentration d'oiseaux aquatiques de l'Île de l'Est 200205 Water fowl gathering area
2068 65216 65216_A CAN CAN True Not Applicable 0.0 Halkett bay park A - Park
11217 308387 308387 CAN CAN False Not Reported 0.0 Aire de concentration d'oiseaux aquatiques pointe au Tonnerre - Île à Paul Water fowl gathering area
4103 306352 306352 CAN CAN False Not Reported 0.0 Aire de concentration d'oiseaux aquatiques de la Baie des Sept Îles 2 Water fowl gathering area
68809455 555621669 55562166

In [12]:
merge.removeMpasByWdpaId(wdpa2remove)

Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Access denied
Carto Error for getting mpa_ids Ac

In [9]:
reload(merge)

<module 'wdpa.merge' from '/Users/russmo/Code/mpatlas-dj2/mpatlas/wdpa/merge.py'>

In [10]:
wdpa2add = merge.getAddWdpaList()

In [11]:
len(wdpa2add)

4184

In [12]:
wdpapid2add = merge.getAddWdpaPidList(verbose=True)

168 wdpa_pid's processed
555516352_A : 1 processed
555637697_A : 2 processed
65386_A : 3 processed
18701_A : 4 processed
555651493_B : 5 processed
555515527_A : 6 processed
555637688_B : 7 processed
555516200_A : 8 processed
357185_A : 9 processed
555637692_B : 10 processed
555566995_B : 11 processed
555515518_B : 12 processed
303295_A : 13 processed
555547863_A : 14 processed
555637700_A : 15 processed
18401_A : 16 processed
555547864_A : 17 processed
67038_A : 18 processed
555547861_B : 19 processed
629_B : 20 processed
555516376_A : 21 processed
18398_A : 22 processed
101417_A : 23 processed
555637693_A : 24 processed
555593900_B : 25 processed
555566999_B : 26 processed
555593737_B : 27 processed
555515516_A : 28 processed
18394_A : 29 processed
13397_A : 30 processed
67347_A : 31 processed
127159_B : 32 processed
555651493_A : 33 processed
13105_A : 34 processed
555548082_B : 35 processed
555566995_A : 36 processed
555515555_A : 37 processed
555547861_C : 38 processed
13390_A : 39

In [13]:
len(wdpapid2add)

168

In [18]:
# Assign records with zones to be the first zone.  Do not rerun.
# In separate notebook

In [14]:
allpid2add = wdpapid2add + [str(int(i)) for i in wdpa2add]
len(allpid2add)
Wdpa2019Poly.objects.filter(wdpa_pid__in=allpid2add).count() + \
Wdpa2019Point.objects.filter(wdpa_pid__in=allpid2add).count()

4320

In [15]:
unmatched_pids_poly = Wdpa2019Poly.objects.filter(
    Q(wdpa_pid__in=allpid2add) | Q(wdpaid__in=wdpa2add)
).exclude(
    wdpa_pid=Func(F('wdpaid'), function='INTEGER', template='(%(expressions)s::%(function)s)::text')
)
unmatched_pids_point = Wdpa2019Point.objects.filter(
    Q(wdpa_pid__in=allpid2add) | Q(wdpaid__in=wdpa2add)
).exclude(
    wdpa_pid=Func(F('wdpaid'), function='INTEGER', template='(%(expressions)s::%(function)s)::text')
)
unmatched_pids_poly.order_by('wdpa_pid').values_list('wdpaid', 'wdpa_pid')


<QuerySet [(101417.0, '101417_A'), (101534.0, '101534_A'), (101586.0, '101586_B'), (101640.0, '101640_A'), (101667.0, '101667_A'), (101683.0, '101683_A'), (101713.0, '101713_A'), (102534.0, '102534_A'), (127159.0, '127159_A'), (127159.0, '127159_B'), (127159.0, '127159_C'), (127159.0, '127159_D'), (13102.0, '13102_A'), (13105.0, '13105_A'), (13107.0, '13107_A'), (13115.0, '13115_A'), (13390.0, '13390_A'), (13391.0, '13391_A'), (13394.0, '13394_A'), (13395.0, '13395_A'), '...(remaining elements truncated)...']>

In [16]:
# Set wdpa_pid for new zones
# If existing MPAtlas sites with this wdpa_id,
# set first non-rejected site to the first PID_A.
# Clear pid for all other MPAtlas sites and flag
# as orphaned zones.

wzones = []
mpasw = [float(wi) for wi in mpaset.filter(wdpa_id__isnull=False).order_by('wdpa_id').values_list('wdpa_id', flat=True)]
polyset = Wdpa2019Poly.objects.filter(wdpaid__in=mpasw).only('wdpaid', 'wdpa_pid', 'name', 'desig_eng', 'iso3', 'parent_iso3')
for w in polyset:
    if w.wdpa_pid != str(int(w.wdpaid)):
        wzones.append(w.wdpaid)
wzones = list(set(wzones))
len(wzones)

432

In [18]:
# Assign mpa records that were previously unzoned to have the pid of the first zone in the updated WDPA data set for this site.
count = 0
for wid in wzones:
    zones = Wdpa2019Poly.objects.filter(wdpaid=wid).only('wdpaid', 'wdpa_pid', 'name', 'desig_eng', 'iso3', 'parent_iso3')
    firstpid = zones.order_by('wdpa_pid').first().wdpa_pid
    mpaz = mpaset.filter(wdpa_id=int(wid)).order_by('mpa_id')
    m = None
    if mpaz.filter(wdpa_pid=firstpid).count() == 0:
        # no mpas match first zone pid
        if mpaz.count() == 1:
            if mpaz[0].wdpa_pid == str(mpaz[0].wdpa_id) or mpaz[0].wdpa_pid == '' or mpaz[0].wdpa_pid is None:
                # only record without specific zone, so go ahead and set it first zone
                m = mpaz[0]
        else:
            if mpaz.count() == mpaz.filter(Q(wdpa_pid=Func(F('wdpa_id'), function='INTEGER', template='(%(expressions)s::%(function)s)::text')) | Q(wdpa_pid__isnull=True) | Q(wdpa_pid='')).count():
                # more than one mpatlas mpa record with this wdpa_id
                # but none have a proper wdpa_pid different from the wdpa_id
                # so set first one to have the first zone pid
                nonrejects = mpaz.exclude(verification_state='Rejected as MPA').order_by('mpa_id')
                if nonrejects:
                    m = nonrejects[0]
                else:
                    m = mpaz[0]
    if m:
        print(m.mpa_id, m.wdpa_id, m.wdpa_pid)
        m.wdpa_pid = firstpid
        count += 1
        print(count, m.mpa_id, m.wdpa_id, m.wdpa_pid)
        m.save()


In [17]:
reload(merge)
# addpoint_geolog = '/home/mpatlas/workspace/log/addpoint_CEA_2019_log.json'
# addpoly_log = '/home/mpatlas/workspace/log/addpoly_CEA_2019_log.json'
# addpoly_geolog = '/home/mpatlas/workspace/log/addpoly_CEA_2019_geo_log.json'
addpoint_geolog = '/Users/russmo/Code/wdpa/log/addpoint_nonCEA_2019_log.json'
addpoly_log = '/Users/russmo/Code/wdpa/log/addpoly_nonCEA_2019_v2_zerogeofix_log.json'
addpoly_geolog = '/Users/russmo/Code/wdpa/log/addpoly_nonCEA_2019_v2_zerogeofix_geo_log.json'

In [27]:
points = Wdpa2019Point.objects.filter(wdpa_pid__in=allpid2add).order_by('wdpa_pid')
merge.updateMpasFromWdpaQueryset(qs=points, poly=False, logfile=None, geologfile=addpoint_geolog, dryrun=False)

1/206 adding/updating wdpa_pid 101172 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813473:  'NoneType' object has no attribute 'hexewkb'
2/206 adding/updating wdpa_pid 101177 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813474:  'NoneType' object has no attribute 'hexewkb'
3/206 adding/updating wdpa_pid 101838 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813475:  'NoneType' object has no attribute 'hexewkb'
4/206 adding/updating wdpa_pid 1051 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813476:  'NoneType' object has no attribute 'hexewkb'
5/206 adding/updating wdpa_pid 107333 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813477:  'NoneType' object has no attribute 'hexewkb'
6/206 adding/updating wdpa_pid 10769 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813478:  'NoneType' object has no att

53/206 adding/updating wdpa_pid 157649 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813525:  'NoneType' object has no attribute 'hexewkb'
54/206 adding/updating wdpa_pid 158677 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813526:  'NoneType' object has no attribute 'hexewkb'
55/206 adding/updating wdpa_pid 159482 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813527:  'NoneType' object has no attribute 'hexewkb'
56/206 adding/updating wdpa_pid 159484 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813528:  'NoneType' object has no attribute 'hexewkb'
57/206 adding/updating wdpa_pid 159486 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813529:  'NoneType' object has no attribute 'hexewkb'
58/206 adding/updating wdpa_pid 159488 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813530:  'NoneType' object h

101/206 adding/updating wdpa_pid 201080 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813573:  'NoneType' object has no attribute 'hexewkb'
102/206 adding/updating wdpa_pid 201081 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813574:  'NoneType' object has no attribute 'hexewkb'
103/206 adding/updating wdpa_pid 201082 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813575:  'NoneType' object has no attribute 'hexewkb'
104/206 adding/updating wdpa_pid 201084 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813576:  'NoneType' object has no attribute 'hexewkb'
105/206 adding/updating wdpa_pid 201085 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813577:  'NoneType' object has no attribute 'hexewkb'
106/206 adding/updating wdpa_pid 201094 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813578:  'NoneType' ob

ERROR processing mpa 68813624:  'NoneType' object has no attribute 'hexewkb'
153/206 adding/updating wdpa_pid 478038 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813625:  'NoneType' object has no attribute 'hexewkb'
154/206 adding/updating wdpa_pid 5055 with mpa_id 5973
    PID: 5055 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 5973:  'NoneType' object has no attribute 'hexewkb'
155/206 adding/updating wdpa_pid 5056 with mpa_id 5974
    PID: 5056 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 5974:  'NoneType' object has no attribute 'hexewkb'
156/206 adding/updating wdpa_pid 555547579 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813626:  'NoneType' object has no attribute 'hexewkb'
157/206 adding/updating wdpa_pid 555552170 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813627:  'NoneType' object has no attribute 'hexewkb'
158

203/206 adding/updating wdpa_pid 900902 with mpa_id 7335
    PID: 900902 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7335:  'NoneType' object has no attribute 'hexewkb'
204/206 adding/updating wdpa_pid 901232 with mpa_id 7345
    PID: 901232 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7345:  'NoneType' object has no attribute 'hexewkb'
205/206 adding/updating wdpa_pid 98379 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813673:  'NoneType' object has no attribute 'hexewkb'
206/206 adding/updating wdpa_pid 98383 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68813674:  'NoneType' object has no attribute 'hexewkb'


True

In [20]:
# post_save.disconnect(mpa_post_save, sender=Mpa)
polys = Wdpa2019Poly.objects.filter(wdpa_pid__in=allpid2add).order_by('wdpa_pid')
merge.updateMpasFromWdpaQueryset(qs=polys, poly=True, logfile=addpoly_log, geologfile=None, dryrun=False)
# post_save.connect(mpa_post_save, sender=Mpa)

1/4123 adding/updating wdpa_pid 101417_A with mpa_id 2619
    PID: 101417_A has 1 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: name orig_name no_take marine
Carto Error for mpa_id 2619: Access denied
2/4123 adding/updating wdpa_pid 101534_A with mpa_id 2623
    PID: 101534_A has 1 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: name orig_name calc_m_area no_take marine
Carto Error for mpa_id 2623: Access denied
3/4123 adding/updating wdpa_pid 101586_B with mpa_id 68813675
    INFO: Older WDPA record not found
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68813675: Access denied
4/4123 adding/updating wdpa_pid 101640_A with mpa_id 2628
    PID: 101640_A has 1 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: name or

    Geom areas similar (2.0111258280156226e-14%), using WDPA boundaries
    Retained old MPAtlas values for: calc_m_area no_take marine
Carto Error for mpa_id 866: Access denied
32/4123 adding/updating wdpa_pid 11006 with mpa_id 868
    PID: 11006 has 1 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: name orig_name calc_m_area no_take marine
Carto Error for mpa_id 868: Access denied
33/4123 adding/updating wdpa_pid 11048 with mpa_id 871
    PID: 11048 has 1 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: name orig_name no_take marine
Carto Error for mpa_id 871: Access denied
34/4123 adding/updating wdpa_pid 11051 with mpa_id 68813682
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: name orig_name no_take marine
Carto Error for mpa_id 68813682: Access denied
35/4123 adding/updating wdpa_pid 11061 with mpa_id 87

Carto Error for mpa_id 68813701: Access denied
66/4123 adding/updating wdpa_pid 127645 with mpa_id 68813702
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: no_take marine
Carto Error for mpa_id 68813702: Access denied
67/4123 adding/updating wdpa_pid 12965 with mpa_id 1049
    PID: 12965 has 8 field diffs  and GEOM diff
    Geom areas 53.79087766642883% dissimilar, keeping existing MPAtlas boundaries
    Retained old MPAtlas values for: status_year rep_area calc_area calc_m_area no_take no_take_area marine own_type mgmt_auth geom
Carto Error for mpa_id 1049: Access denied
68/4123 adding/updating wdpa_pid 12988 with mpa_id 68813703
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: no_take marine
Carto Error for mpa_id 68813703: Access denied
69/4123 adding/updating wdpa_pid 1305 with mpa_id 171
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: no_take marine
Carto Er

Carto Error for mpa_id 68813705: Access denied
94/4123 adding/updating wdpa_pid 134968 with mpa_id 68813706
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: designation designation_eng no_take marine
Carto Error for mpa_id 68813706: Access denied
95/4123 adding/updating wdpa_pid 134971 with mpa_id 68813707
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: designation designation_eng no_take marine
Carto Error for mpa_id 68813707: Access denied
96/4123 adding/updating wdpa_pid 134989 with mpa_id 68813708
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: name orig_name designation designation_eng no_take marine
Carto Error for mpa_id 68813708: Access denied
97/4123 adding/updating wdpa_pid 134997 with mpa_id 68813709
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: name orig_name designation designation_eng no_take marine
Carto 

    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: name orig_name designation designation_eng calc_m_area no_take marine
Carto Error for mpa_id 68813739: Access denied
128/4123 adding/updating wdpa_pid 135564 with mpa_id 68813740
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: designation designation_eng no_take marine
Carto Error for mpa_id 68813740: Access denied
129/4123 adding/updating wdpa_pid 135574 with mpa_id 68813741
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: name orig_name designation designation_eng calc_m_area no_take marine
Carto Error for mpa_id 68813741: Access denied
130/4123 adding/updating wdpa_pid 135576 with mpa_id 68813742
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: name orig_name designation designation_eng no_take marine
Carto Error for mpa_id 68813742: Access denied
131/4123 adding/updating 

...

Carto Error for mpa_id 68817148: Access denied
4002/4123 adding/updating wdpa_pid 67243 with mpa_id 68817149
    MPAtlas orig geom area is zero, using WDPA boundaries
    Retained old MPAtlas values for: calc_m_area mgmt_plan_ref no_take iucn_category marine own_type mgmt_auth
Carto Error for mpa_id 68817149: Access denied
4003/4123 adding/updating wdpa_pid 67244 with mpa_id 68817150
    MPAtlas orig geom area is zero, using WDPA boundaries
    Retained old MPAtlas values for: calc_m_area mgmt_plan_ref no_take iucn_category marine own_type mgmt_auth
Carto Error for mpa_id 68817150: Access denied
4004/4123 adding/updating wdpa_pid 67245 with mpa_id 68817151
    MPAtlas orig geom area is zero, using WDPA boundaries
    Retained old MPAtlas values for: mgmt_plan_ref no_take iucn_category marine mgmt_auth
Carto Error for mpa_id 68817151: Access denied
4005/4123 adding/updating wdpa_pid 67253 with mpa_id 68817152
    MPAtlas orig geom area is zero, using WDPA boundaries
    Retained old MPA

Carto Error for mpa_id 2331: Access denied
4030/4123 adding/updating wdpa_pid 68169 with mpa_id 2333
    PID: 68169 has 4 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: designation designation_eng rep_m_area rep_area calc_m_area no_take marine
Carto Error for mpa_id 2333: Access denied
4031/4123 adding/updating wdpa_pid 68848 with mpa_id 68817165
    MPAtlas orig geom area is zero, using WDPA boundaries
    Retained old MPAtlas values for: no_take marine
Carto Error for mpa_id 68817165: Access denied
4032/4123 adding/updating wdpa_pid 70931 with mpa_id 2404
    PID: 70931 has 9 field diffs  and GEOM diff
    Geom areas 0.009963512962767986% dissimilar, keeping existing MPAtlas boundaries
    Retained old MPAtlas values for: status_year rep_area calc_area calc_m_area no_take no_take_area iucn_category marine own_type mgmt_auth geom
Carto Error for mpa_id 2404: Access denied
4033/4123 adding/updating wdpa_pid 8012 with mpa_id 606
  

Carto Error for mpa_id 68817189: Access denied
4062/4123 adding/updating wdpa_pid 83159 with mpa_id 68817190
    MPAtlas orig geom area is zero, using WDPA boundaries
    Retained old MPAtlas values for: designation designation_eng no_take marine
Carto Error for mpa_id 68817190: Access denied
4063/4123 adding/updating wdpa_pid 83160 with mpa_id 68817191
    MPAtlas orig geom area is zero, using WDPA boundaries
    Retained old MPAtlas values for: name orig_name designation designation_eng no_take marine
Carto Error for mpa_id 68817191: Access denied
4064/4123 adding/updating wdpa_pid 83164 with mpa_id 68817192
    MPAtlas orig geom area is zero, using WDPA boundaries
    Retained old MPAtlas values for: name orig_name designation designation_eng no_take marine
Carto Error for mpa_id 68817192: Access denied
4065/4123 adding/updating wdpa_pid 83169 with mpa_id 68817193
    MPAtlas orig geom area is zero, using WDPA boundaries
    Retained old MPAtlas values for: designation designation_e

Carto Error for mpa_id 68817212: Access denied
4093/4123 adding/updating wdpa_pid 92627 with mpa_id 68817213
    MPAtlas orig geom area is zero, using WDPA boundaries
    Retained old MPAtlas values for: status_year no_take marine gov_type mgmt_auth
Carto Error for mpa_id 68817213: Access denied
4094/4123 adding/updating wdpa_pid 92927 with mpa_id 68817214
    MPAtlas orig geom area is zero, using WDPA boundaries
    Retained old MPAtlas values for: name orig_name calc_m_area no_take marine
Carto Error for mpa_id 68817214: Access denied
4095/4123 adding/updating wdpa_pid 92950 with mpa_id 68817215
    MPAtlas orig geom area is zero, using WDPA boundaries
    Retained old MPAtlas values for: name orig_name no_take marine
Carto Error for mpa_id 68817215: Access denied
4096/4123 adding/updating wdpa_pid 92955 with mpa_id 68817216
    MPAtlas orig geom area is zero, using WDPA boundaries
    Retained old MPAtlas values for: no_take marine
Carto Error for mpa_id 68817216: Access denied
4097

True

In [21]:
bad = Wdpa2019Poly.objects.get(wdpa_pid='555643543')
bg = bad.geom
bg.num_coords
555643544
bad = Wdpa2019Poly.objects.get(wdpa_pid='555643544')
bg = bad.geom
bg.num_coords

2833100

In [18]:
reload(merge)
# updatepoint_geolog = '/home/mpatlas/workspace/log/updatepoint_GBR_log.json'
# updatepoly_log = '/home/mpatlas/workspace/log/updatepoly_GBR_log.json'
# updatepoly_geolog = '/home/mpatlas/workspace/log/updatepoly_GBR_geo_log.json'
updatepoint_geolog = '/Users/russmo/Code/wdpa/log/updatepoint_nonCEA_2019_v3_geo_log.json'
updatepoly_log = '/Users/russmo/Code/wdpa/log/updatepoly_nonCEA_2019_v3_log.json'
updatepoly_geolog = '/Users/russmo/Code/wdpa/log/updatepoly_nonCEA_2019_v3_geo_log.json'

In [19]:
# wdpa_filter = (
# #     Q(iso3__icontains='USA') | Q(parent_iso3__icontains='USA') |
# #     Q(iso3__icontains='UMI') | Q(parent_iso3__icontains='UMI') |
# #     Q(iso3__icontains='VIR') | Q(parent_iso3__icontains='VIR') |
# #     Q(iso3__icontains='PRI') | Q(parent_iso3__icontains='PRI') |
# #     Q(iso3__icontains='ASM') | Q(parent_iso3__icontains='ASM') |
# #     Q(iso3__icontains='GUM') | Q(parent_iso3__icontains='GUM') |
# #     Q(iso3__icontains='MNP') | Q(parent_iso3__icontains='MNP') |
#     Q(iso3__icontains='MEX') | Q(iso3__icontains='CHL') | Q(iso3__icontains='IDN') | 
#     Q(iso3__icontains='CHN') | Q(iso3__icontains='JPN') | 
#     Q(parent_iso3__icontains='MEX') | Q(parent_iso3__icontains='CHL') | Q(parent_iso3__icontains='IDN') |
#     Q(parent_iso3__icontains='CHN') | Q(parent_iso3__icontains='JPN') #|
# #     Q(iso3__icontains='FRA') | Q(parent_iso3__icontains='FRA') |
# #     Q(iso3__icontains='ATF') | Q(iso3__icontains='BLM') | Q(iso3__icontains='GLP') |
# #     Q(iso3__icontains='GUF') | Q(iso3__icontains='MAF') | Q(iso3__icontains='MTQ') |
# #     Q(iso3__icontains='MYT') | Q(iso3__icontains='NCL') | Q(iso3__icontains='PYF') |
# #     Q(iso3__icontains='REU') | Q(iso3__icontains='SHN') | Q(iso3__icontains='SYC') |
# #     Q(iso3__icontains='AUS') | Q(parent_iso3__icontains='AUS') |
# #     Q(iso3__icontains='ZAF') | Q(parent_iso3__icontains='ZAF') |
# #     Q(iso3__icontains='CAN') | Q(parent_iso3__icontains='CAN') |
# #     Q(iso3__icontains='GBR') | Q(parent_iso3__icontains='GBR') |
# #     Q(iso3__icontains='AIA') | Q(iso3__icontains='BMU') | Q(iso3__icontains='CYM') |
# #     Q(iso3__icontains='FLK') | Q(iso3__icontains='GIB') | Q(iso3__icontains='IMN') |
# #     Q(iso3__icontains='IOT') | Q(iso3__icontains='JEY') | Q(iso3__icontains='MSR') |
# #     Q(iso3__icontains='PCN') | Q(iso3__icontains='SGS') | Q(iso3__icontains='SHN') |
# #     Q(iso3__icontains='TCA') | Q(iso3__icontains='VGB')
# )
wdpa_filter = (
    Q()
)
wdpa_exclude = (
    Q(iso3__icontains='USA') | Q(parent_iso3__icontains='USA') |
    Q(iso3__icontains='UMI') | Q(parent_iso3__icontains='UMI') |
    Q(iso3__icontains='VIR') | Q(parent_iso3__icontains='VIR') |
    Q(iso3__icontains='PRI') | Q(parent_iso3__icontains='PRI') |
    Q(iso3__icontains='ASM') | Q(parent_iso3__icontains='ASM') |
    Q(iso3__icontains='GUM') | Q(parent_iso3__icontains='GUM') |
    Q(iso3__icontains='MNP') | Q(parent_iso3__icontains='MNP') |
    Q(iso3__icontains='MEX') | Q(iso3__icontains='CHL') | Q(iso3__icontains='IDN') | 
    Q(iso3__icontains='CHN') | Q(iso3__icontains='JPN') | 
    Q(parent_iso3__icontains='MEX') | Q(parent_iso3__icontains='CHL') | Q(parent_iso3__icontains='IDN') |
    Q(parent_iso3__icontains='CHN') | Q(parent_iso3__icontains='JPN')
)
polys = Wdpa2019Poly.objects.exclude(wdpa_pid__in=allpid2add).exclude(wdpa_exclude).filter(wdpa_filter).filter(marine__in=('1','2')).order_by('wdpa_pid').values_list('wdpa_pid', flat=True)
points = Wdpa2019Point.objects.exclude(wdpa_pid__in=allpid2add).exclude(wdpa_exclude).filter(wdpa_filter).filter(marine__in=('1','2')).order_by('wdpa_pid').values_list('wdpa_pid', flat=True)
allpid2update = list(set(list(polys) + list(points)))

polys_nonmarine = Wdpa2019Poly.objects.exclude(wdpa_pid__in=allpid2add).exclude(wdpa_exclude).filter(wdpa_filter).filter(marine__in=('0')).order_by('wdpa_pid').values_list('wdpa_pid', flat=True)
points_nonmarine = Wdpa2019Point.objects.exclude(wdpa_pid__in=allpid2add).exclude(wdpa_exclude).filter(wdpa_filter).filter(marine__in=('0')).order_by('wdpa_pid').values_list('wdpa_pid', flat=True)
allpid2update_nonmarine = list(set(list(polys_nonmarine) + list(points_nonmarine)))

allpid2update_nonmarine_inmpatlas = mpaset.filter(wdpa_pid__in=allpid2update_nonmarine).order_by('wdpa_pid').values_list('wdpa_pid', flat=True)

allpid2update_marine012 = allpid2update + list(allpid2update_nonmarine_inmpatlas)

In [20]:
print('marine:', len(allpid2update), 'nonmarine:', len(allpid2update_nonmarine), 'all:', len(allpid2update_marine012))
print('POINTS --', 
      'marine:', Wdpa2019Point.objects.filter(wdpa_pid__in=allpid2update).count(),
      'nonmarine:', Wdpa2019Point.objects.filter(wdpa_pid__in=allpid2update_nonmarine).count()
)
print('POLYGONS --', 
      'marine:', Wdpa2019Poly.objects.filter(wdpa_pid__in=allpid2update).count(),
      'nonmarine:', Wdpa2019Poly.objects.filter(wdpa_pid__in=allpid2update_nonmarine).count(),
)
print('MPATLAS Records --', 
      'marine:', mpaset.filter(wdpa_pid__in=allpid2update).count(),
      'nonmarine:', mpaset.filter(wdpa_pid__in=allpid2update_nonmarine).count(),
)

marine: 11026 nonmarine: 188991 all: 14659
POINTS -- marine: 405 nonmarine: 19736
POLYGONS -- marine: 10621 nonmarine: 169255
MPATLAS Records -- marine: 11485 nonmarine: 3633


In [28]:
len(set(allpid2update_marine012))

14552

In [26]:
# All marine=1,2 sites and only marine=0 that exist in MPAtlas
updatepoints = Wdpa2019Point.objects.filter(wdpa_pid__in=allpid2update_marine012).order_by('wdpa_pid')
merge.updateMpasFromWdpaQueryset(qs=updatepoints, poly=False, logfile=None, geologfile=updatepoint_geolog, dryrun=False)

1/798 adding/updating wdpa_pid 10010 with mpa_id 6026
    PID: 10010 has 1 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6026:  'NoneType' object has no attribute 'hexewkb'
2/798 adding/updating wdpa_pid 10059 with mpa_id 6027
    PID: 10059 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6027:  'NoneType' object has no attribute 'hexewkb'
3/798 adding/updating wdpa_pid 10093 with mpa_id 6028
    PID: 10093 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6028:  'NoneType' object has no attribute 'hexewkb'
4/798 adding/updating wdpa_pid 10098 with mpa_id 6031
    PID: 10098 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6031:  'NoneType' object has no attribute 'hexewkb'
5/798 adding/updating wdpa_pid 10170 with mpa_id 6032
    PID: 10170 has 6 field diffs 
    Retained old MPAtlas values for: name designation designation_eng
ERROR processing mpa 6032:  'NoneType' object 

    Retained old MPAtlas values for: 
ERROR processing mpa 6170:  'NoneType' object has no attribute 'hexewkb'
43/798 adding/updating wdpa_pid 13208 with mpa_id 6171
    PID: 13208 has 1 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6171:  'NoneType' object has no attribute 'hexewkb'
44/798 adding/updating wdpa_pid 13209 with mpa_id 6172
    PID: 13209 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6172:  'NoneType' object has no attribute 'hexewkb'
45/798 adding/updating wdpa_pid 13210 with mpa_id 6173
    PID: 13210 has 1 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6173:  'NoneType' object has no attribute 'hexewkb'
46/798 adding/updating wdpa_pid 13211 with mpa_id 6174
    PID: 13211 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6174:  'NoneType' object has no attribute 'hexewkb'
47/798 adding/updating wdpa_pid 13212 with mpa_id 6175
    PID: 13212 has 3 field diffs 


    Retained old MPAtlas values for: 
ERROR processing mpa 6211:  'NoneType' object has no attribute 'hexewkb'
84/798 adding/updating wdpa_pid 13250 with mpa_id 6212
    PID: 13250 has 1 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6212:  'NoneType' object has no attribute 'hexewkb'
85/798 adding/updating wdpa_pid 13251 with mpa_id 6213
    PID: 13251 has 1 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6213:  'NoneType' object has no attribute 'hexewkb'
86/798 adding/updating wdpa_pid 13252 with mpa_id 6214
    PID: 13252 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6214:  'NoneType' object has no attribute 'hexewkb'
87/798 adding/updating wdpa_pid 13253 with mpa_id 6215
    PID: 13253 has 1 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6215:  'NoneType' object has no attribute 'hexewkb'
88/798 adding/updating wdpa_pid 13254 with mpa_id 6216
    PID: 13254 has 1 field diffs 


    Retained old MPAtlas values for: 
ERROR processing mpa 6321:  'NoneType' object has no attribute 'hexewkb'
126/798 adding/updating wdpa_pid 14261 with mpa_id 6322
    PID: 14261 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6322:  'NoneType' object has no attribute 'hexewkb'
127/798 adding/updating wdpa_pid 14262 with mpa_id 6323
    PID: 14262 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6323:  'NoneType' object has no attribute 'hexewkb'
128/798 adding/updating wdpa_pid 14263 with mpa_id 6324
    PID: 14263 has 1 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6324:  'NoneType' object has no attribute 'hexewkb'
129/798 adding/updating wdpa_pid 14266 with mpa_id 6325
    PID: 14266 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6325:  'NoneType' object has no attribute 'hexewkb'
130/798 adding/updating wdpa_pid 14268 with mpa_id 6326
    PID: 14268 has 1 field di

    Retained old MPAtlas values for: 
ERROR processing mpa 6386:  'NoneType' object has no attribute 'hexewkb'
167/798 adding/updating wdpa_pid 17182 with mpa_id 6387
    PID: 17182 has 1 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6387:  'NoneType' object has no attribute 'hexewkb'
168/798 adding/updating wdpa_pid 17188 with mpa_id 6388
    PID: 17188 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6388:  'NoneType' object has no attribute 'hexewkb'
169/798 adding/updating wdpa_pid 17189 with mpa_id 6389
    PID: 17189 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6389:  'NoneType' object has no attribute 'hexewkb'
170/798 adding/updating wdpa_pid 17239 with mpa_id 6393
    PID: 17239 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6393:  'NoneType' object has no attribute 'hexewkb'
171/798 adding/updating wdpa_pid 17258 with mpa_id 6395
    PID: 17258 has 3 field di

...

    PID: 555555595 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 9688:  'NoneType' object has no attribute 'hexewkb'
654/798 adding/updating wdpa_pid 555580794 with mpa_id 68810690
    PID: 555580794 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 68810690:  'NoneType' object has no attribute 'hexewkb'
655/798 adding/updating wdpa_pid 555580795 with mpa_id 68810691
    PID: 555580795 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 68810691:  'NoneType' object has no attribute 'hexewkb'
656/798 adding/updating wdpa_pid 555580796 with mpa_id 68810692
    PID: 555580796 has 1 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 68810692:  'NoneType' object has no attribute 'hexewkb'
657/798 adding/updating wdpa_pid 555580797 with mpa_id 68810693
    PID: 555580797 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 68810693:  'NoneType' object has no att

    Retained old MPAtlas values for: 
ERROR processing mpa 6729:  'NoneType' object has no attribute 'hexewkb'
694/798 adding/updating wdpa_pid 68327 with mpa_id 6737
    PID: 68327 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6737:  'NoneType' object has no attribute 'hexewkb'
695/798 adding/updating wdpa_pid 71023 with mpa_id 6742
    PID: 71023 has 1 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6742:  'NoneType' object has no attribute 'hexewkb'
696/798 adding/updating wdpa_pid 71023 with mpa_id 7706742
    PID: 71023 has 1 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7706742:  'NoneType' object has no attribute 'hexewkb'
697/798 adding/updating wdpa_pid 71025 with mpa_id 7706744
    PID: 71025 has 1 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7706744:  'NoneType' object has no attribute 'hexewkb'
698/798 adding/updating wdpa_pid 71025 with mpa_id 6744
    PID: 71025 ha

    Retained old MPAtlas values for: 
ERROR processing mpa 7313:  'NoneType' object has no attribute 'hexewkb'
735/798 adding/updating wdpa_pid 900815 with mpa_id 7318
    PID: 900815 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7318:  'NoneType' object has no attribute 'hexewkb'
736/798 adding/updating wdpa_pid 900823 with mpa_id 7319
    PID: 900823 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7319:  'NoneType' object has no attribute 'hexewkb'
737/798 adding/updating wdpa_pid 900825 with mpa_id 7320
    PID: 900825 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7320:  'NoneType' object has no attribute 'hexewkb'
738/798 adding/updating wdpa_pid 900847 with mpa_id 7328
    PID: 900847 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7328:  'NoneType' object has no attribute 'hexewkb'
739/798 adding/updating wdpa_pid 900848 with mpa_id 7329
    PID: 900848 has 

    Retained old MPAtlas values for: 
ERROR processing mpa 7434:  'NoneType' object has no attribute 'hexewkb'
776/798 adding/updating wdpa_pid 902855 with mpa_id 7435
    PID: 902855 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7435:  'NoneType' object has no attribute 'hexewkb'
777/798 adding/updating wdpa_pid 902855 with mpa_id 7707435
    PID: 902855 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7707435:  'NoneType' object has no attribute 'hexewkb'
778/798 adding/updating wdpa_pid 902909 with mpa_id 7444
    PID: 902909 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7444:  'NoneType' object has no attribute 'hexewkb'
779/798 adding/updating wdpa_pid 902910 with mpa_id 7445
    PID: 902910 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7445:  'NoneType' object has no attribute 'hexewkb'
780/798 adding/updating wdpa_pid 9048 with mpa_id 6007
    PID: 9048 ha

True

In [22]:
reload(merge)
# All marine=1,2 sites and only marine=0 that exist in MPAtlas
updatepolys = Wdpa2019Poly.objects.filter(wdpa_pid__in=allpid2update_marine012).order_by('wdpa_pid')
updatepolys = updatepolys.exclude(wdpa_pid__in=partialrunids)
merge.updateMpasFromWdpaQueryset(qs=updatepolys, poly=True, logfile=updatepoly_log, geologfile=None, dryrun=False)

1/3237 adding/updating wdpa_pid 555565830 with mpa_id 15143
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15143: Access denied
2/3237 adding/updating wdpa_pid 555566859 with mpa_id 15144
    PID: 555566859 has 3 field diffs  and GEOM diff
    Geom areas similar (2.109580232188275e-14%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15144: Access denied
3/3237 adding/updating wdpa_pid 555566860 with mpa_id 15145
    PID: 555566860 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15145: Access denied
4/3237 adding/updating wdpa_pid 555566861 with mpa_id 15146
    PID: 555566861 has 3 field diffs  and GEOM diff
    Geom areas similar (2.288429521847774e-14%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15146: Access denied
5/3237 adding/updating wdpa_

    INFO: Older WDPA record not found
    Geom areas 9.23418082723879% dissimilar, keeping existing MPAtlas boundaries
    Retained old MPAtlas values for: geom
Carto Error for mpa_id 15174: Access denied
33/3237 adding/updating wdpa_pid 555567012 with mpa_id 15175
    PID: 555567012 has 6 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15175: Access denied
34/3237 adding/updating wdpa_pid 555567013 with mpa_id 15176
    PID: 555567013 has 7 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15176: Access denied
35/3237 adding/updating wdpa_pid 555567014 with mpa_id 15177
    PID: 555567014 has 6 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15177: Access denied
36/3237 adding/updating wdpa_pid 555567022 with mpa

    PID: 555567558 has 6 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15208: Access denied
66/3237 adding/updating wdpa_pid 555567561 with mpa_id 15209
    PID: 555567561 has 6 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15209: Access denied
67/3237 adding/updating wdpa_pid 555567563 with mpa_id 15210
    PID: 555567563 has 6 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15210: Access denied
68/3237 adding/updating wdpa_pid 555567565 with mpa_id 15211
    PID: 555567565 has 6 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15211: Access denied
69/3237 adding/updating wdpa_pid 555567566 with mpa_id 15212
    PID:

    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15242: Access denied
99/3237 adding/updating wdpa_pid 555567630 with mpa_id 15243
    PID: 555567630 has 7 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15243: Access denied
100/3237 adding/updating wdpa_pid 555567632 with mpa_id 15244
    PID: 555567632 has 8 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15244: Access denied
101/3237 adding/updating wdpa_pid 555567634 with mpa_id 15246
    PID: 555567634 has 6 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15246: Access denied
102/3237 adding/updating wdpa_pid 555567635 with mpa_id 15247
    PID: 555567635 has 8 field diffs  and GEOM diff
    G

    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15277: Access denied
132/3237 adding/updating wdpa_pid 555569932 with mpa_id 15278
    PID: 555569932 has 6 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 15278: Access denied
133/3237 adding/updating wdpa_pid 555570013 with mpa_id 68812268
    PID: 555570013 has 3 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68812268: Access denied
134/3237 adding/updating wdpa_pid 555570014 with mpa_id 68812269
    PID: 555570014 has 3 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68812269: Access denied
135/3237 adding/updating wdpa_pid 555570029 with mpa_id 68812270
    PID: 555570029 has 3 field diffs 
    Geom areas similar (0.0%), 

...

3120/3237 adding/updating wdpa_pid 95302 with mpa_id 7702529
    PID: 95302 has 3 field diffs  and GEOM diff
    Geom areas similar (1.2391699302123858e-14%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 7702529: Access denied
3121/3237 adding/updating wdpa_pid 95303 with mpa_id 2530
    PID: 95303 has 3 field diffs  and GEOM diff
    Geom areas similar (3.074463423980302e-14%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 2530: Access denied
3122/3237 adding/updating wdpa_pid 95303 with mpa_id 7702530
    PID: 95303 has 3 field diffs  and GEOM diff
    Geom areas similar (3.074463423980302e-14%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 7702530: Access denied
3123/3237 adding/updating wdpa_pid 95304 with mpa_id 6775
    PID: 95304 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for 

    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 2551: Access denied
3155/3237 adding/updating wdpa_pid 95382 with mpa_id 2552
    PID: 95382 has 4 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 2552: Access denied
3156/3237 adding/updating wdpa_pid 95384 with mpa_id 9832
    PID: 95384 has 4 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 9832: Access denied
3157/3237 adding/updating wdpa_pid 95385 with mpa_id 2553
    PID: 95385 has 2 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 2553: Access denied
3158/3237 adding/updating wdpa_pid 95393 with mpa_id 2554
    PID: 95393 has 2 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto

    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68813297: Access denied
3191/3237 adding/updating wdpa_pid 9820 with mpa_id 763
    PID: 9820 has 2 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 763: Access denied
3192/3237 adding/updating wdpa_pid 9821 with mpa_id 68813298
    PID: 9821 has 1 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68813298: Access denied
3193/3237 adding/updating wdpa_pid 9822 with mpa_id 764
    PID: 9822 has 1 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 764: Access denied
3194/3237 adding/updating wdpa_pid 9861 with mpa_id 765
    PID: 9861 has 1 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto 

    PID: 99751_A has 6 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 2597: Access denied
3226/3237 adding/updating wdpa_pid 99751_B with mpa_id 68809518
    PID: 99751_B has 7 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68809518: Access denied
3227/3237 adding/updating wdpa_pid 99755 with mpa_id 2598
    PID: 99755 has 5 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 2598: Access denied
3228/3237 adding/updating wdpa_pid 99806_B with mpa_id 68809519
    PID: 99806_B has 5 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68809519: Access denied
3229/3237 adding/updating wdpa_pid 99829_A with mpa_id 2600
    PID: 998

True

In [31]:
mpids = mpaset.filter(wdpa_id__isnull=False, wdpa_pid__isnull=False)
mpids_count = mpids.count()
count = 0
for m in mpids:
    count += 1
    try:
        w = Wdpa2019Poly.objects.filter(wdpa_pid=m.wdpa_pid)
    except:
        try:
            w = Wdpa2019Point.objects.filter(wdpa_pid=m.wdpa_pid)
        except:
            pass
    if w.exists():
        w0 = w[0]
        mq = mpaset.filter(pk=m.pk)
        print('%s/%s mpa_id %s wdpa_pid %s updated with _wdpa values' % (count, mpids_count, m.mpa_id, w0.wdpa_pid))
        mq.update(
            no_take_wdpa=w0.no_take,
            no_take_area_wdpa=w0.no_tk_area,
        )

1/19455 mpa_id 68812255 wdpa_pid 555563177 updated with _wdpa values
2/19455 mpa_id 68811823 wdpa_pid 555539677 updated with _wdpa values
3/19455 mpa_id 11578 wdpa_pid 346091 updated with _wdpa values
4/19455 mpa_id 68812256 wdpa_pid 555563181 updated with _wdpa values
5/19455 mpa_id 11626 wdpa_pid 356589 updated with _wdpa values
6/19455 mpa_id 68811918 wdpa_pid 555540601 updated with _wdpa values
7/19455 mpa_id 2130 wdpa_pid 67301 updated with _wdpa values
8/19455 mpa_id 10781 wdpa_pid 175375 updated with _wdpa values
9/19455 mpa_id 11581 wdpa_pid 346096 updated with _wdpa values
10/19455 mpa_id 12480 wdpa_pid 555517837 updated with _wdpa values
11/19455 mpa_id 68812257 wdpa_pid 555563182 updated with _wdpa values
12/19455 mpa_id 6761 wdpa_pid 81027 updated with _wdpa values
13/19455 mpa_id 6762 wdpa_pid 81028 updated with _wdpa values
14/19455 mpa_id 10782 wdpa_pid 175381 updated with _wdpa values
15/19455 mpa_id 68812258 wdpa_pid 555563186 updated with _wdpa values
16/19455 mpa_id 

126/19455 mpa_id 15138 wdpa_pid 555563467 updated with _wdpa values
127/19455 mpa_id 2839 wdpa_pid 127892 updated with _wdpa values
128/19455 mpa_id 68811836 wdpa_pid 555539727 updated with _wdpa values
129/19455 mpa_id 2149 wdpa_pid 67742 updated with _wdpa values
130/19455 mpa_id 68811838 wdpa_pid 555539733 updated with _wdpa values
131/19455 mpa_id 2496 wdpa_pid 81058 updated with _wdpa values
132/19455 mpa_id 68811839 wdpa_pid 555539734 updated with _wdpa values
133/19455 mpa_id 68811842 wdpa_pid 555539742 updated with _wdpa values
134/19455 mpa_id 3290 wdpa_pid 160873 updated with _wdpa values
135/19455 mpa_id 68811843 wdpa_pid 555539748 updated with _wdpa values
136/19455 mpa_id 227 wdpa_pid 1754 updated with _wdpa values
137/19455 mpa_id 68810795 wdpa_pid 160877 updated with _wdpa values
138/19455 mpa_id 10789 wdpa_pid 175400 updated with _wdpa values
139/19455 mpa_id 12482 wdpa_pid 555517840 updated with _wdpa values
140/19455 mpa_id 10791 wdpa_pid 175403 updated with _wdpa val

251/19455 mpa_id 12492 wdpa_pid 555517874 updated with _wdpa values
252/19455 mpa_id 2164 wdpa_pid 67811 updated with _wdpa values
253/19455 mpa_id 4015 wdpa_pid 305988 updated with _wdpa values
254/19455 mpa_id 2165 wdpa_pid 67817 updated with _wdpa values
255/19455 mpa_id 68812130 wdpa_pid 555557042 updated with _wdpa values
256/19455 mpa_id 6362 wdpa_pid 16137 updated with _wdpa values
257/19455 mpa_id 2166 wdpa_pid 67819 updated with _wdpa values
258/19455 mpa_id 2167 wdpa_pid 67820 updated with _wdpa values
259/19455 mpa_id 2168 wdpa_pid 67821 updated with _wdpa values
260/19455 mpa_id 2169 wdpa_pid 67825 updated with _wdpa values
261/19455 mpa_id 2170 wdpa_pid 67826 updated with _wdpa values
262/19455 mpa_id 68812695 wdpa_pid 555592998 updated with _wdpa values
263/19455 mpa_id 11044 wdpa_pid 183295 updated with _wdpa values
264/19455 mpa_id 2171 wdpa_pid 67833 updated with _wdpa values
265/19455 mpa_id 68811858 wdpa_pid 555539780 updated with _wdpa values
266/19455 mpa_id 15181 

375/19455 mpa_id 67706139 wdpa_pid 12837 updated with _wdpa values
376/19455 mpa_id 15186 wdpa_pid 555567037 updated with _wdpa values
377/19455 mpa_id 68811115 wdpa_pid 339598 updated with _wdpa values
378/19455 mpa_id 5885 wdpa_pid 3371 updated with _wdpa values
379/19455 mpa_id 15892 wdpa_pid 555578836 updated with _wdpa values
380/19455 mpa_id 15893 wdpa_pid 555578837 updated with _wdpa values
381/19455 mpa_id 68810803 wdpa_pid 161435 updated with _wdpa values
382/19455 mpa_id 13762 wdpa_pid 555539887 updated with _wdpa values
383/19455 mpa_id 1267 wdpa_pid 16154 updated with _wdpa values
384/19455 mpa_id 2190 wdpa_pid 67876 updated with _wdpa values
385/19455 mpa_id 2191 wdpa_pid 67877 updated with _wdpa values
386/19455 mpa_id 2192 wdpa_pid 67878 updated with _wdpa values
387/19455 mpa_id 15187 wdpa_pid 555567038 updated with _wdpa values
388/19455 mpa_id 2193 wdpa_pid 67879 updated with _wdpa values
389/19455 mpa_id 7701268 wdpa_pid 16179 updated with _wdpa values
390/19455 mpa_

501/19455 mpa_id 13776 wdpa_pid 555539925 updated with _wdpa values
502/19455 mpa_id 1012 wdpa_pid 12888 updated with _wdpa values
503/19455 mpa_id 68808207 wdpa_pid 555594040 updated with _wdpa values
504/19455 mpa_id 13777 wdpa_pid 555539926 updated with _wdpa values
505/19455 mpa_id 13778 wdpa_pid 555539927 updated with _wdpa values
506/19455 mpa_id 3986 wdpa_pid 305890 updated with _wdpa values
507/19455 mpa_id 2224 wdpa_pid 67912 updated with _wdpa values
508/19455 mpa_id 1013 wdpa_pid 12896 updated with _wdpa values
509/19455 mpa_id 7414 wdpa_pid 902768 updated with _wdpa values
510/19455 mpa_id 68811337 wdpa_pid 555517980 updated with _wdpa values
511/19455 mpa_id 2225 wdpa_pid 67913 updated with _wdpa values
512/19455 mpa_id 7075 wdpa_pid 312886 updated with _wdpa values
513/19455 mpa_id 67706150 wdpa_pid 12902 updated with _wdpa values
514/19455 mpa_id 10933 wdpa_pid 182915 updated with _wdpa values
515/19455 mpa_id 7418 wdpa_pid 902793 updated with _wdpa values
516/19455 mpa_

...

18972/19455 mpa_id 4880 wdpa_pid 342403 updated with _wdpa values
18973/19455 mpa_id 212 wdpa_pid 1578 updated with _wdpa values
18974/19455 mpa_id 11124 wdpa_pid 194955 updated with _wdpa values
18975/19455 mpa_id 7701246 wdpa_pid 15781 updated with _wdpa values
18976/19455 mpa_id 4881 wdpa_pid 342404 updated with _wdpa values
18977/19455 mpa_id 12470 wdpa_pid 555517793 updated with _wdpa values
18978/19455 mpa_id 15594 wdpa_pid 555577254 updated with _wdpa values
18979/19455 mpa_id 13873 wdpa_pid 555540559 updated with _wdpa values
18980/19455 mpa_id 2826 wdpa_pid 127856 updated with _wdpa values
18981/19455 mpa_id 1246 wdpa_pid 15781 updated with _wdpa values
18982/19455 mpa_id 15595 wdpa_pid 555577256 updated with _wdpa values
18983/19455 mpa_id 13676 wdpa_pid 555539274 updated with _wdpa values
18984/19455 mpa_id 13677 wdpa_pid 555539275 updated with _wdpa values
18985/19455 mpa_id 4882 wdpa_pid 342405 updated with _wdpa values
18986/19455 mpa_id 11125 wdpa_pid 194956 updated with

19091/19455 mpa_id 15155 wdpa_pid 555566870 updated with _wdpa values
19092/19455 mpa_id 15156 wdpa_pid 555566871 updated with _wdpa values
19093/19455 mpa_id 15157 wdpa_pid 555566872 updated with _wdpa values
19094/19455 mpa_id 15158 wdpa_pid 555566873 updated with _wdpa values
19095/19455 mpa_id 15162 wdpa_pid 555566877 updated with _wdpa values
19096/19455 mpa_id 68810289 wdpa_pid 555560481 updated with _wdpa values
19097/19455 mpa_id 68810290 wdpa_pid 555560482 updated with _wdpa values
19098/19455 mpa_id 10814 wdpa_pid 175495 updated with _wdpa values
19099/19455 mpa_id 12475 wdpa_pid 555517824 updated with _wdpa values
19100/19455 mpa_id 68809492 wdpa_pid 67054_B updated with _wdpa values
19101/19455 mpa_id 6575 wdpa_pid 32568 updated with _wdpa values
19102/19455 mpa_id 68810291 wdpa_pid 555560483 updated with _wdpa values
19103/19455 mpa_id 11032 wdpa_pid 183275 updated with _wdpa values
19104/19455 mpa_id 68810293 wdpa_pid 555560485 updated with _wdpa values
19105/19455 mpa_id

19210/19455 mpa_id 68811210 wdpa_pid 378101 updated with _wdpa values
19211/19455 mpa_id 68810856 wdpa_pid 170658 updated with _wdpa values
19212/19455 mpa_id 2112 wdpa_pid 67268 updated with _wdpa values
19213/19455 mpa_id 4915 wdpa_pid 351753 updated with _wdpa values
19214/19455 mpa_id 11624 wdpa_pid 356417 updated with _wdpa values
19215/19455 mpa_id 3945 wdpa_pid 305706 updated with _wdpa values
19216/19455 mpa_id 68811199 wdpa_pid 352551 updated with _wdpa values
19217/19455 mpa_id 68809403 wdpa_pid 555566976_B updated with _wdpa values
19218/19455 mpa_id 4955 wdpa_pid 352710 updated with _wdpa values
19219/19455 mpa_id 13706 wdpa_pid 555539382 updated with _wdpa values
19220/19455 mpa_id 9799 wdpa_pid 67269 updated with _wdpa values
19221/19455 mpa_id 13707 wdpa_pid 555539383 updated with _wdpa values
19222/19455 mpa_id 5132 wdpa_pid 354006 updated with _wdpa values
19223/19455 mpa_id 68812230 wdpa_pid 555562158 updated with _wdpa values
19224/19455 mpa_id 68812231 wdpa_pid 5555

19330/19455 mpa_id 9805 wdpa_pid 67281 updated with _wdpa values
19331/19455 mpa_id 68812245 wdpa_pid 555562535 updated with _wdpa values
19332/19455 mpa_id 11272 wdpa_pid 311868 updated with _wdpa values
19333/19455 mpa_id 4420 wdpa_pid 311871 updated with _wdpa values
19334/19455 mpa_id 13726 wdpa_pid 555539439 updated with _wdpa values
19335/19455 mpa_id 68811258 wdpa_pid 389088 updated with _wdpa values
19336/19455 mpa_id 68809095 wdpa_pid 555539440 updated with _wdpa values
19337/19455 mpa_id 5166 wdpa_pid 356523 updated with _wdpa values
19338/19455 mpa_id 68809500 wdpa_pid 67282 updated with _wdpa values
19339/19455 mpa_id 5801 wdpa_pid 555539441 updated with _wdpa values
19340/19455 mpa_id 68812246 wdpa_pid 555562585 updated with _wdpa values
19341/19455 mpa_id 13727 wdpa_pid 555539442 updated with _wdpa values
19342/19455 mpa_id 13730 wdpa_pid 555539445 updated with _wdpa values
19343/19455 mpa_id 68809097 wdpa_pid 555539547 updated with _wdpa values
19344/19455 mpa_id 3990 wd

19448/19455 mpa_id 11507 wdpa_pid 341918 updated with _wdpa values
19449/19455 mpa_id 1251 wdpa_pid 15986 updated with _wdpa values
19450/19455 mpa_id 2835 wdpa_pid 127884 updated with _wdpa values
19451/19455 mpa_id 68811818 wdpa_pid 555539633 updated with _wdpa values
19452/19455 mpa_id 2129 wdpa_pid 67299 updated with _wdpa values
19453/19455 mpa_id 1252 wdpa_pid 15990 updated with _wdpa values
19454/19455 mpa_id 9745 wdpa_pid 15991 updated with _wdpa values
19455/19455 mpa_id 10958 wdpa_pid 183036 updated with _wdpa values


mpaset.filter(wdpa_pid__isnull=False).update(
    no_take_wdpa=F('no_take'), no_take_area_wdpa=F('no_take_area')
)

In [82]:
nt = ('All', 'Part', 'None')
ntupdate = mpaset.filter(wdpa_pid__isnull=False).filter(
    (~Q(no_take_wdpa__in=('All')) & Q(no_take_mpatlas__in=('All')))
    | (~Q(no_take_wdpa__in=('All', 'Part')) & Q(no_take_mpatlas__in=('All', 'Part')))
    | (Q(no_take_wdpa__in=('Not Applicable')) & Q(no_take_mpatlas__in=('All', 'Part', 'None')))
)
ntupdate.update(no_take=F('no_take_mpatlas'))

5

In [83]:
ntareaupdate = mpaset.filter(wdpa_pid__isnull=False).filter(
    Q(no_take_area_mpatlas__isnull=False) &
    (
        Q(no_take_area_wdpa__isnull=True)
        | Q(no_take_area_mpatlas__gt=F('no_take_area_wdpa'))
    )
)
ntareaupdate.update(no_take_area=F('no_take_area_mpatlas'))

2

In [84]:
ntchanges = ntupdate | ntareaupdate
for n in ntchanges:
    print(n.mpa_id, n.wdpa_id, n.wdpa_pid, n.name, n.designation, n.designation_eng, n.no_take_wdpa, n.no_take_mpatlas, n.no_take_area_wdpa, n.no_take_area_mpatlas)

1198 14553 14553 Meagre Bay Pond Animal Sanctuary Animal Sanctuary Animal Sanctuary Not Applicable All 0.0 0.0
7701198 14553 14553 Meagre Bay Pond Animal Sanctuary Animal Sanctuary Animal Sanctuary Not Applicable All 0.0 None
67701872 36094 36094 Columbus Landfall Marine National Park National Park Not Reported All 0.0 None
1199 14554 14554 Colliers Bay Pond Animal Sanctuary Animal Sanctuary Animal Sanctuary Not Applicable All 0.0 0.0
15067 555559204 555559204 Medway Estuary Marine Conservation Zone Marine Conservation Zone Not Reported Not Reported 0.0 12.1
1201 14557 14557 Booby Pond Nature Reserve Booby Pond Nature Reserve Booby Pond Nature Reserve Not Applicable All 0.0 1.0


In [85]:
ntchanges = ntupdate | ntareaupdate

import csv

with open('/home/mpatlas/workspace/log/notakechange_GBR_log.csv', 'w', newline='') as csvfile:
    fieldnames = ['mpa_id', 'wdpa_id', 'wdpa_pid', 'name', 'designation', 'designation_eng', 'no_take_wdpa', 'no_take_mpatlas', 'no_take_area_wdpa', 'no_take_area_mpatlas']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

    writer.writeheader()
    for row in ntchanges.values(*fieldnames):
        writer.writerow(row)

In [86]:
for n in ntchanges:
    try:
        w2019 = Wdpa2019Poly.objects.get(wdpa_pid=n.wdpa_pid)
    except:
        w2019 = Wdpa2019Point.objects.get(wdpa_pid=n.wdpa_pid)
    try:
        w2018 = Wdpa2018Polygon.objects.filter(wdpa_pid=n.wdpa_pid)[0]
    except:
        try:
            w2018 = Wdpa2018Point.objects.filter(wdpa_pid=n.wdpa_pid)[0]
        except:
            try:
                w2018 = Wdpa2018Polygon.objects.filter(wdpaid=n.wdpa_id)[0]
            except:
                w2018 = Wdpa2018Point.objects.filter(wdpaid=n.wdpa_id)[0]
    if (n.no_take == w2018.no_take) or (n.no_take_area == w2018.no_tk_area):
        print(w2019.name, w2019.desig, n.no_take_mpatlas, w2019.no_take, w2018.no_take, n.no_take_area_mpatlas, w2019.no_tk_area, w2018.no_tk_area)

Meagre Bay Pond Animal Sanctuary Animal Sanctuary All Not Applicable Not Applicable 0.0 0.0 0.0
Meagre Bay Pond Animal Sanctuary Animal Sanctuary All Not Applicable Not Applicable None 0.0 0.0
Columbus Landfall Marine National Park All Not Reported Not Applicable None 0.0 0.0
Colliers Bay Pond Animal Sanctuary Animal Sanctuary All Not Applicable Not Applicable 0.0 0.0 0.0


In [87]:
ntchanges2 = ntupdate | ntareaupdate
ntchanges.count()

6

In [95]:
mpaset = mpas_all_nogeom.exclude(
        Q(country__icontains='USA') | Q(sovereign__icontains='USA') |
        Q(country__icontains='UMI') | Q(sovereign__icontains='UMI') |
        Q(country__icontains='VIR') | Q(sovereign__icontains='VIR') |
        Q(country__icontains='PRI') | Q(sovereign__icontains='PRI') |
        Q(country__icontains='ASM') | Q(sovereign__icontains='ASM') |
        Q(country__icontains='GUM') | Q(sovereign__icontains='GUM') |
        Q(country__icontains='MNP') | Q(sovereign__icontains='MNP')
    ).exclude(
        Q(country__icontains='MEX') | Q(country__icontains='CHL') | Q(country__icontains='IDN') | 
        Q(country__icontains='CHN') | Q(country__icontains='JPN') | 
        Q(sovereign__icontains='MEX') | Q(sovereign__icontains='CHL') | Q(sovereign__icontains='IDN') |
        Q(sovereign__icontains='CHN') | Q(sovereign__icontains='JPN')
    ).exclude(
        Q(country__icontains='FRA') | Q(sovereign__icontains='FRA') |
        Q(country__icontains='ATF') | Q(country__icontains='BLM') | Q(country__icontains='GLP') |
        Q(country__icontains='GUF') | Q(country__icontains='MAF') | Q(country__icontains='MTQ') |
        Q(country__icontains='MYT') | Q(country__icontains='NCL') | Q(country__icontains='PYF') |
        Q(country__icontains='REU') | Q(country__icontains='SHN') | Q(country__icontains='SYC')
    ).exclude(
        Q(country__icontains='AUS') | Q(sovereign__icontains='AUS') |
        Q(country__icontains='ZAF') | Q(sovereign__icontains='ZAF') |
        Q(country__icontains='CAN') | Q(sovereign__icontains='CAN')
    ).exclude(
        Q(country__icontains='GBR') | Q(sovereign__icontains='GBR') |
        Q(country__icontains='AIA') | Q(country__icontains='BMU') | Q(country__icontains='CYM') |
        Q(country__icontains='FLK') | Q(country__icontains='GIB') | Q(country__icontains='IMN') |
        Q(country__icontains='IOT') | Q(country__icontains='JEY') | Q(country__icontains='MSR') |
        Q(country__icontains='PCN') | Q(country__icontains='SGS') | Q(country__icontains='SHN') |
        Q(country__icontains='TCA') | Q(country__icontains='VGB')
    )

from mpatlas.utils import cartompa
cartompa.purgeCartoMpas()

[188,
 195,
 498,
 500,
 504,
 512,
 513,
 514,
 515,
 995,
 1429,
 1431,
 1434,
 1435,
 1436,
 1437,
 1438,
 1440,
 1445,
 1503,
 1505,
 1508,
 1509,
 1510,
 1511,
 1513,
 1851,
 1872,
 2362,
 2363,
 2364,
 2365,
 2366,
 2367,
 2369,
 2370,
 2371,
 2375,
 2378,
 2510,
 2517,
 2518,
 2519,
 2522,
 2524,
 3582,
 3819,
 3820,
 3823,
 3824,
 6871,
 6884,
 6935,
 6936,
 6938,
 6942,
 6943,
 6945,
 6946,
 6948,
 6949,
 6952,
 6955,
 6956,
 6957,
 7270,
 7283,
 7299,
 9280,
 9397,
 9398,
 9399,
 9400,
 9401,
 9402,
 9403,
 9405,
 9406,
 9407,
 9408,
 9409,
 9410,
 9411,
 9412,
 9413,
 9414,
 9415,
 9416,
 9417,
 9418,
 9419,
 9420,
 9421,
 9422,
 15058,
 15083,
 7700994,
 7700999,
 7701851,
 7702510,
 7702516,
 7702520,
 7702521,
 7703821,
 7703822,
 7703825,
 7703826,
 7705349,
 7709259]

In [94]:
cartompa.updateAllMpas(mpas=mpaset)

Processing 10 of 1987 mpa records at a time
Records [0 - 9]
Records [10 - 19]
Records [20 - 29]
Records [30 - 39]
ERROR processing mpa 68807503:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 68807503
Records [40 - 49]
ERROR processing mpa 68807520:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 68807520
ERROR processing mpa 68807504:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 68807504
Records [50 - 59]
Records [60 - 69]
ERROR processing mpa 68807500:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 68807500
ERROR processing mpa 68807495:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 68807495
ERROR processing mpa 60009586:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 60009586
ERROR processing mpa 60009547:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 60009547
ERROR processing mpa 60009546:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 60009546
ERROR processing mpa 60009495:  'NoneTyp

KeyboardInterrupt: 